In [1]:
import pandas as pd
import igraph as ig 
import seaborn as sns
import numpy as np
import lzma
from Bio import Align

In [2]:
#using readlines to ensure the file is read as a list of lines
with lzma.open('data/sequences.txt.xz', 'rt', encoding='utf-8') as f:
    sequences = f.readlines()

In [3]:
aligner = Align.PairwiseAligner()
aligner.substitution_matrix = Align.substitution_matrices.load("BLOSUM62")
aligner.mode = "global"


In [4]:
nsequence = len(sequences)
similarity_matrix = np.zeros((nsequence, nsequence))

In [5]:
max_scores = np.zeros(nsequence)
for i in range(nsequence):
    seq = sequences[i].strip()
    # S_i,i is the maximum score for sequence i
    max_scores[i] = aligner.score(seq, seq)

In [6]:
sequences[0]

'KRLFDLTLSVLILPFVLPLMGIIALAIKLDSPGPVLYRARRVGENGKLFYMLKFRTMVQDADKRLHEVMQTDEQGNLVYKRPDDPRVTRVGRFLRRTSLDELPQLFNVLRGEMSLVGPRPELPELVERYALWQRKRFAVPQGITGWWQINGRADKPMHLHTEDDLYYVQNYSLWLDLLILWRTFWAVLR\n'

In [7]:
for i in range(nsequence): 
    seq_i_cleaned = str(sequences[i]).strip()
    S_max_i = max_scores[i]
    for j in range(nsequence): 
        seq_j_cleaned = str(sequences[j]).strip()

        score = aligner.score(seq_i_cleaned, seq_j_cleaned)
        similarity_matrix[i, j] = score

In [8]:
similarity_matrix

array([[998., 132., 194., ..., 555.,  95.,  83.],
       [132., 515., 132., ..., 137.,  95., 129.],
       [194., 132., 914., ..., 228., 112.,  95.],
       ...,
       [555., 137., 228., ..., 960., 105., 100.],
       [ 95.,  95., 112., ..., 105., 441.,  90.],
       [ 83., 129.,  95., ..., 100.,  90., 440.]], shape=(513, 513))

In [26]:
diag = np.diag(similarity_matrix)

# 3. Calculate the normalization denominator
# We need a matrix where position (i, j) = sqrt(diag[i] * diag[j])
# The outer product is efficient for creating this grid of values.
denominator = np.sqrt(np.outer(diag, diag))

# 4. Perform element-wise division
normalized_matrix = similarity_matrix / denominator

# # --- Verification ---
# # The diagonal should now be all 1.0s
# print("Diagonal check (should be all 1s):")
# print(np.diag(normalized_matrix)[:5]) 

# # Inspect the result
# print("\nNormalized Matrix (first 3x3):")
# print(np.round(normalized_matrix[:3, :3], 3))

mini=normalized_matrix[:5, :5]

In [27]:
mini

array([[1.        , 0.18412173, 0.20312499, 0.1623589 , 0.1497555 ],
       [0.18412173, 1.        , 0.19239652, 0.29540591, 0.21454237],
       [0.20312499, 0.19239652, 1.        , 0.15328535, 0.1716786 ],
       [0.1623589 , 0.29540591, 0.15328535, 1.        , 0.24178715],
       [0.1497555 , 0.21454237, 0.1716786 , 0.24178715, 1.        ]])

In [18]:
num_sequences = normalized_matrix.shape[0]
edges = [(i, j) for i in range(num_sequences) for j in range(i + 1, num_sequences) if
            normalized_matrix[i, j] > 0.4]
graph = ig.Graph()
graph.add_vertices(num_sequences)
graph.add_edges(edges)

In [19]:
communities = graph.community_infomap()
print(communities.membership)

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 3, 6, 10, 11, 5, 12, 5, 6, 13, 14, 2, 6, 2, 5, 6, 2, 0, 2, 2, 15, 6, 16, 0, 0, 0, 0, 17, 18, 17, 14, 14, 17, 6, 2, 2, 3, 19, 6, 0, 0, 6, 0, 6, 6, 0, 2, 2, 2, 0, 6, 0, 0, 6, 2, 6, 2, 20, 0, 21, 14, 2, 2, 6, 5, 22, 6, 22, 22, 2, 23, 0, 0, 0, 0, 23, 0, 0, 3, 3, 23, 0, 5, 15, 24, 15, 14, 25, 15, 0, 0, 0, 26, 27, 26, 0, 0, 15, 0, 26, 26, 5, 6, 0, 0, 28, 26, 0, 29, 26, 26, 14, 26, 6, 15, 6, 6, 30, 6, 14, 14, 30, 0, 30, 26, 31, 0, 0, 6, 14, 0, 14, 26, 0, 6, 6, 0, 15, 14, 14, 14, 32, 14, 14, 33, 34, 0, 0, 0, 14, 26, 2, 0, 0, 0, 0, 26, 0, 35, 14, 0, 30, 36, 14, 0, 35, 14, 14, 5, 14, 37, 5, 0, 0, 35, 35, 0, 37, 35, 0, 14, 15, 38, 0, 39, 15, 40, 0, 0, 14, 15, 14, 14, 0, 39, 14, 39, 39, 37, 0, 0, 39, 41, 15, 39, 0, 42, 15, 0, 39, 15, 15, 15, 37, 39, 14, 15, 14, 39, 37, 39, 14, 0, 0, 39, 0, 0, 37, 14, 37, 14, 25, 14, 14, 0, 0, 39, 15, 14, 14, 0, 14, 39, 15, 5, 14, 14, 39, 39, 0, 0, 0, 0, 39, 39, 37, 39, 14, 14, 37, 43, 44, 45, 45, 15, 15, 0, 45, 15, 15, 37, 46, 37, 45

In [20]:
import seaborn

rainbow = seaborn.color_palette("husl", len(communities))
colours = [rainbow[communities.membership[v]] for v in graph.vs.indices]
graph.vs["color"] = colours

In [21]:
plot = ig.plot(graph, bbox=(1280, 1280), layout="fr", target = "stable_network_04t.png")

In [22]:
plot

In [16]:
degrees = graph.degree()
pd.DataFrame(degrees).describe()

0
count  513.000000
mean    87.598441
std     40.886354
min      1.000000
25%     50.000000
50%     97.000000
75%    133.000000
max    137.000000

In [17]:
graph.vs["size"] = 10 + 2 * pd.qcut(degrees, 8, labels=False)


ValueError: Bin edges must be unique: Index([1.0, 25.0, 50.0, 87.0, 97.0, 103.0, 133.0, 133.0, 137.0], dtype='float64').
You can drop duplicate edges by setting the 'duplicates' kwarg

In [ ]:
ig.plot(graph, bbox=(1280, 1280), layout="fr")

In [ ]:
def analyze_network(graph):
    return {
        "Number of Nodes": graph.vcount(),
        "Number of Edges": graph.ecount(),
        "Average Degree": sum(graph.degree()) / graph.vcount(),
        "Clustering Coefficient": graph.transitivity_undirected(),
        "Number of Connected Components": len(graph.components())
    }

analyze_network(graph)

{'Number of Nodes': 513,
 'Number of Edges': 9758,
 'Average Degree': 38.04288499025341,
 'Clustering Coefficient': 0.9014949622397535,
 'Number of Connected Components': 61}